In [3]:
pip install -U vnstock

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [1]:
print("vnstock package installed successfully.")

vnstock package installed successfully.


In [2]:
print("vnstock package installed successfully.")

vnstock package installed successfully.


In [4]:
pip install optuna

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [5]:
pip install ta

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [6]:
pip install tensorflow

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [7]:
pip install keras-self-attention

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [8]:
pip install keras-tuner

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [9]:
pip install importlib-metadata

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [10]:
import numpy as np
import pandas as pd
from ta.momentum import RSIIndicator
from sklearn.preprocessing import RobustScaler
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dropout, Dense, RNN, concatenate
from tensorflow.keras.optimizers import RMSprop
from vnstock import *
from ta.volatility import BollingerBands
from tensorflow.keras.layers import Layer
import tensorflow as tf
from keras.layers import Input, Conv1D, MaxPooling1D, Bidirectional, Flatten, BatchNormalization
from sklearn.model_selection import RandomizedSearchCV
# from scikeras.wrappers import KerasClassifier

from ta.momentum import StochasticOscillator
from ta.volume import OnBalanceVolumeIndicator
from ta.trend import CCIIndicator
from sklearn.preprocessing import StandardScaler
from ta.volume import ChaikinMoneyFlowIndicator
from tensorflow.keras.regularizers import l2
from tensorflow.keras.regularizers import l1
from tensorflow.keras.regularizers import l1_l2
from tensorflow.keras import regularizers
# from keras_self_attention import SeqSelfAttention
from tensorflow.keras.models import Model
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import roc_auc_score
import keras_tuner as kt
from tensorflow.keras.optimizers import Adam
from sklearn.feature_selection import SequentialFeatureSelector
from sklearn.base import BaseEstimator, ClassifierMixin
from tensorflow.keras.saving import register_keras_serializable
import matplotlib.pyplot as plt
from imblearn.over_sampling import SMOTE
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint, ReduceLROnPlateau

In [11]:
import os

In [12]:
from datetime import datetime, timedelta

In [13]:
from vnstock import *
import pandas as pd
import os
from collections import Counter
from tensorflow.keras.models import load_model
from sklearn.metrics import classification_report
from sklearn.utils.class_weight import compute_class_weight
from sklearn.ensemble import RandomForestClassifier # Import RandomForestClassifier
from sklearn.metrics import accuracy_score # Import accuracy_score

In [14]:
from sklearn.linear_model import LinearRegression

In [15]:
pip install xgboost

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [16]:
from sklearn.metrics import log_loss
from xgboost import XGBClassifier
import optuna
import joblib

IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html


In [17]:
def load_stock(symbol, folder_path='stock_data'):
    """
    Load dữ liệu cổ phiếu từ mã cổ phiếu, sử dụng đường dẫn thư mục cố định.

    Parameters:
        symbol (str): Mã cổ phiếu (ví dụ: 'VCB')
        folder_path (str): Thư mục chứa file Excel (mặc định là 'stock_data')

    Returns:
        DataFrame chứa dữ liệu cổ phiếu.
    """
    file_path = os.path.join(folder_path, f"{symbol}.xlsx")

    if not os.path.exists(file_path):
        raise FileNotFoundError(f"❌ Không tìm thấy file: {file_path}")

    try:
        df = pd.read_excel(file_path)
        print(f"✅ Đã load dữ liệu cho mã: {symbol}")
        return df
    except Exception as e:
        print(f"❌ Lỗi khi load dữ liệu {symbol}: {e}")
        return pd.DataFrame()

In [ ]:
def load_and_process_data(symbol, drop_na=True, folder_path = ''):
    data = load_stock(symbol,folder_path)
    if data.empty:
        return None

    df = data

    columns_to_drop = ['EV/EBITDA_Previous_Quarter','EV/EBITDA_Same_Period_Last_Year','ROIC (%)_Previous_Quarter','ROIC (%)_Same_Period_Last_Year']  # thay bằng danh sách cột bạn muốn xóa
    # doi ten o day
    
    df.drop(columns=columns_to_drop, inplace=True)

     # Tính toán khối lượng trung bình
    volume_ma_period = 20  # Ví dụ: khối lượng trung bình 20 ngày
    df['volume_ma'] = df['volume'].rolling(window=volume_ma_period).mean()


    # Tính tỷ lệ khối lượng hiện tại / khối lượng trung bình
    df['volume_to_volume_ma_ratio'] = df['volume'] / df['volume_ma']


    # Tính toán EMA ngắn hạn (12 ngày)
    df['ema_12'] = df['close'].ewm(span=12, adjust=False).mean()


    # Tính toán EMA dài hạn (26 ngày)
    df['ema_26'] = df['close'].ewm(span=26, adjust=False).mean()

    # Tính toán SMA trung hạn (20 ngày)
    df['sma_20'] = df['close'].rolling(window=20).mean()

    # Tính toán SMA dài hạn (50 ngày)
    df['sma_50'] = df['close'].rolling(window=50).mean()

     # Tính toán ROC

    df['roc_1'] = ((df['close'] - df['close'].shift(1)) / df['close'].shift(1)) * 100
    df['roc_5'] = ((df['close'] - df['close'].shift(5)) / df['close'].shift(5)) * 100
    df['roc_9'] = ((df['close'] - df['close'].shift(9)) / df['close'].shift(9)) * 100

    # Tính toán %K (Stochastic Oscillator)
    stoch_period = 14
    df['%K'] = ((df['close'] - df['low'].rolling(window=stoch_period).min()) /
                (df['high'].rolling(window=stoch_period).max() - df['low'].rolling(window=stoch_period).min())) * 100

    # Tính toán %R (Williams %R)
    df['%R'] = ((df['high'].rolling(window=stoch_period).max() - df['close']) /
                (df['high'].rolling(window=stoch_period).max() - df['low'].rolling(window=stoch_period).min())) * -100

    # Tính toán CCI (Commodity Channel Index)
    cci_period = 20
    df['typical_price'] = (df['high'] + df['low'] + df['close']) / 3
    df['cci'] = CCIIndicator(high=df['high'], low=df['low'], close=df['close'], window=cci_period).cci()

    # Tính toán OBV (On Balance Volume)
    df['obv'] = OnBalanceVolumeIndicator(close=df['close'], volume=df['volume']).on_balance_volume()


    # Tính toán MACD
    df['macd'] = df['ema_12'] - df['ema_26']
    # Tính toán Signal line (EMA 9 ngày của MACD)
    df['signal_line'] = df['macd'].ewm(span=9, adjust=False).mean()
    # Tính toán MACD histogram
    df['macd_histogram'] = df['macd'] - df['signal_line']


    # Tính toán RSI
    rsi_period = 14
    df['rsi'] = RSIIndicator(df['close'], window=rsi_period).rsi()
    ma_period = 9
    df['rsi_base_ma'] = df['rsi'].rolling(window=ma_period).mean()
    df['rsi_rsi_base_ma_ratio'] = df['rsi'] / df['rsi_base_ma']


    # Bollinger Bands
    indicator_bb = BollingerBands(close=df['close'], window=20, window_dev=2)
    df['bb_bbm'] = indicator_bb.bollinger_mavg()
    df['bb_bbh'] = indicator_bb.bollinger_hband()
    df['bb_bbl'] = indicator_bb.bollinger_lband()
    df['bb_bbp'] = indicator_bb.bollinger_pband()

    df['bb_bbh_bb_bbl_ratio'] = df['bb_bbh'] / df['bb_bbl']

    df['hl_ratio'] = df['high'] / (df['low'] + 1e-8)
    df['co_ratio'] = df['close'] / (df['open'] + 1e-8)
    df['price_range'] = (df['high'] - df['low']) / (df['close'] + 1e-8)

    if 'sma_20' in df.columns and 'sma_50' in df.columns:
        df['sma_ratio_20_50'] = df['sma_20'] / (df['sma_50'] + 1e-8)
    if 'ema_12' in df.columns and 'ema_26' in df.columns:
        df['ema_ratio_12_26'] = df['ema_12'] / (df['ema_26'] + 1e-8)

    if all(col in df.columns for col in ['bb_bbh', 'bb_bbl', 'bb_bbm']):
        df['bb_width'] = (df['bb_bbh'] - df['bb_bbl']) / (df['bb_bbm'] + 1e-8)
        df['bb_position'] = (df['close'] - df['bb_bbl']) / (df['bb_bbh'] - df['bb_bbl'] + 1e-8)

    if 'rsi' in df.columns:
        df['rsi_overbought'] = (df['rsi'] > 70).astype(int)
        df['rsi_oversold'] = (df['rsi'] < 30).astype(int)
        df['rsi_neutral'] = ((df['rsi'] >= 30) & (df['rsi'] <= 70)).astype(int)

    if all(col in df.columns for col in ['macd', 'signal_line']):
        df['macd_signal_diff'] = df['macd'] - df['signal_line']
        df['macd_bullish'] = (df['macd'] > df['signal_line']).astype(int)

    for period in [5, 10]:
        if len(df) > period:
            df[f'momentum_{period}'] = df['close'].pct_change(period)

    # =============================================================

    # =======================================================================

    # 1. Daily log return
    df['log_return'] = np.log(df['close'] / df['close'].shift(1))

    # 2. Rolling volatility (biến động trượt)
    for window in [5, 10, 20, 30]:
        df[f'volatility_{window}d'] = df['log_return'].rolling(window=window).std()

    # 3. Rolling mean log return
    for window in [5, 10, 20, 30]:
        df[f'mean_log_return_{window}d'] = df['log_return'].rolling(window=window).mean()

    # 4. Sharpe-like ratio (mean return / volatility)
    for window in [5, 10, 20, 30]:
        mean_col = f'mean_log_return_{window}d'
        vol_col = f'volatility_{window}d'
        df[f'sharpe_like_{window}d'] = df[mean_col] / (df[vol_col] + 1e-9)

    # 5. Directional Feature - chuỗi ngày tăng liên tiếp
    df['up_streak'] = (df['log_return'] > 0).astype(int)
    df['up_streak'] = df['up_streak'] * (df['up_streak'].groupby((df['up_streak'] != df['up_streak'].shift()).cumsum()).cumcount() + 1)
    df['up_streak'] = df['up_streak'].where(df['log_return'] > 0, 0)

    # 6. Tỷ lệ ngày log return dương trong 20 ngày gần nhất
    df['pos_log_return_ratio_20d'] = df['log_return'].rolling(window=20).apply(lambda x: np.mean(x > 0), raw=True)

    # 7. Z-score của log return hiện tại
    for window in [5, 10, 20, 30]:
        mean_col = f'mean_log_return_{window}d'
        vol_col = f'volatility_{window}d'
        df[f'z_score_{window}d'] = (df['log_return'] - df[mean_col]) / (df[vol_col] + 1e-9)



    # Tính Annual Return (lợi nhuận hàng năm)
    df['annual_return'] = df['close'] / df['close'].shift(252) - 1  # 252 ngày giao dịch trong năm

    # Tính Volatility (Độ biến động) hàng năm (Standard Deviation of Returns)
    df['daily_return'] = df['close'].pct_change()  # Tỷ suất lợi nhuận hàng ngày
    df['annual_volatility'] = df['daily_return'].rolling(window=252).std() * (252 ** 0.5)  # Độ lệch chuẩn hàng năm (tính từ tỷ suất lợi nhuận hàng ngày)

    risk_free_rate = 0.03  # tương đương 3%/năm
    # Tính Sharpe ratio: (Rp - Rf) / Volatility
    df['sharpe_ratio'] = (df['annual_return'] - risk_free_rate) / df['annual_volatility']


    # Tính toán chỉ số cơ bản ==========================================================
    df['P/B_change_rate_flag'] = np.where(df['P/B_Same_Period_Last_Year'] == 0, 1, 0)
    df['P/B_change_rate'] = np.where(
        df['P/B_Same_Period_Last_Year'] != 0,
        (df['P/B_Previous_Quarter'] - df['P/B_Same_Period_Last_Year']) / df['P/B_Same_Period_Last_Year'],
        999
    )

    # P/E
    df['P/E_change_rate_flag'] = np.where(df['P/E_Same_Period_Last_Year'] == 0, 1, 0)
    df['P/E_change_rate'] = np.where(
        df['P/E_Same_Period_Last_Year'] != 0,
        (df['P/E_Previous_Quarter'] - df['P/E_Same_Period_Last_Year']) / df['P/E_Same_Period_Last_Year'],
        999
    )

    # P/S
    df['P/S_change_rate_flag'] = np.where(df['P/S_Same_Period_Last_Year'] == 0, 1, 0)
    df['P/S_change_rate'] = np.where(
        df['P/S_Same_Period_Last_Year'] != 0,
        (df['P/S_Previous_Quarter'] - df['P/S_Same_Period_Last_Year']) / df['P/S_Same_Period_Last_Year'],
        999
    )

    # P/Cash Flow
    df['P/Cash Flow_change_rate_flag'] = np.where(df['P/Cash Flow_Same_Period_Last_Year'] == 0, 1, 0)
    df['P/Cash Flow_change_rate'] = np.where(
        df['P/Cash Flow_Same_Period_Last_Year'] != 0,
        (df['P/Cash Flow_Previous_Quarter'] - df['P/Cash Flow_Same_Period_Last_Year']) / df['P/Cash Flow_Same_Period_Last_Year'],
        999
    )

    # EPS (VND)
    df['EPS (VND)_change_rate_flag'] = np.where(df['EPS (VND)_Same_Period_Last_Year'] == 0, 1, 0)
    df['EPS (VND)_change_rate'] = np.where(
        df['EPS (VND)_Same_Period_Last_Year'] != 0,
        (df['EPS (VND)_Previous_Quarter'] - df['EPS (VND)_Same_Period_Last_Year']) / df['EPS (VND)_Same_Period_Last_Year'],
        999
    )

    # BVPS (VND)
    df['BVPS (VND)_change_rate_flag'] = np.where(df['BVPS (VND)_Same_Period_Last_Year'] == 0, 1, 0)
    df['BVPS (VND)_change_rate'] = np.where(
        df['BVPS (VND)_Same_Period_Last_Year'] != 0,
        (df['BVPS (VND)_Previous_Quarter'] - df['BVPS (VND)_Same_Period_Last_Year']) / df['BVPS (VND)_Same_Period_Last_Year'],
        999
    )

    # ROE (%)
    df['ROE (%)_change_rate_flag'] = np.where(df['ROE (%)_Same_Period_Last_Year'] == 0, 1, 0)
    df['ROE (%)_change_rate'] = np.where(
        df['ROE (%)_Same_Period_Last_Year'] != 0,
        (df['ROE (%)_Previous_Quarter'] - df['ROE (%)_Same_Period_Last_Year']) / df['ROE (%)_Same_Period_Last_Year'],
        999
    )

    # ROA (%)
    df['ROA (%)_change_rate_flag'] = np.where(df['ROA (%)_Same_Period_Last_Year'] == 0, 1, 0)
    df['ROA (%)_change_rate'] = np.where(
        df['ROA (%)_Same_Period_Last_Year'] != 0,
        (df['ROA (%)_Previous_Quarter'] - df['ROA (%)_Same_Period_Last_Year']) / df['ROA (%)_Same_Period_Last_Year'],
        999
    )

    # ==================================================================================================


    # Xứ lý với VNINDEX =============================================================================
    data_time = data['time']

    data_vni = load_stock('VNINDEX', folder_path)
    data_vni = data_vni.drop(columns=['ticket'])
    data_vni.columns = ['time','open_vni', 'high_vni', 'low_vni', 'close_vni', 'volume_vni']



    # Tính toán RSI
    rsi_period = 14
    data_vni['rsi_vni'] = RSIIndicator(data_vni['close_vni'], window=rsi_period).rsi()
    # Tính toán RSI-base-MA
    ma_period = 9
    data_vni['rsi_base_ma_vni'] = data_vni['rsi_vni'].rolling(window=ma_period).mean()
    data_vni['rsi_rsi_base_ma_ratio_vni'] = data_vni['rsi_vni'] / data_vni['rsi_base_ma_vni']

    # Tính toán khối lượng trung bình
    volume_ma_period = 20  # Ví dụ: khối lượng trung bình 20 ngày
    data_vni['volume_ma_vni'] = data_vni['volume_vni'].rolling(window=volume_ma_period).mean()
    # Tính tỷ lệ khối lượng hiện tại / khối lượng trung bình
    data_vni['volume_to_volume_ma_ratio_vni'] = data_vni['volume_vni'] / data_vni['volume_ma_vni']

    # Bollinger Bands
    indicator_bb = BollingerBands(close=data_vni['close_vni'], window=20, window_dev=2)
    data_vni['bb_bbm_vni'] = indicator_bb.bollinger_mavg()
    data_vni['bb_bbh_vni'] = indicator_bb.bollinger_hband()
    data_vni['bb_bbl_vni'] = indicator_bb.bollinger_lband()
    data_vni['bb_bbp_vni'] = indicator_bb.bollinger_pband()

    data_vni['bb_bbh_bb_bbl_ratio_vni'] = data_vni['bb_bbh_vni'] / data_vni['bb_bbl_vni']

    

    # Tính toán ROC
    roc_period = 9  # Chu kỳ 9 ngày, bạn có thể thay đổi tùy ý
    # data_vni['roc_vni'] = ((data_vni['close_vni'] - data_vni['close_vni'].shift(roc_period)) / data_vni['close_vni'].shift(roc_period)) * 100
    data_vni['roc_1_vni'] = ((data_vni['close_vni'] - data_vni['close_vni'].shift(1)) / data_vni['close_vni'].shift(1)) * 100
    data_vni['roc_5_vni'] = ((data_vni['close_vni'] - data_vni['close_vni'].shift(5)) / data_vni['close_vni'].shift(5)) * 100
    data_vni['roc_9_vni'] = ((data_vni['close_vni'] - data_vni['close_vni'].shift(9)) / data_vni['close_vni'].shift(9)) * 100
    # Tính toán %K (Stochastic Oscillator)
    stoch_period = 14
    data_vni['%K_vni'] = ((data_vni['close_vni'] - data_vni['low_vni'].rolling(window=stoch_period).min()) /
                (data_vni['high_vni'].rolling(window=stoch_period).max() - data_vni['low_vni'].rolling(window=stoch_period).min())) * 100

    # Tính toán %R (Williams %R)
    data_vni['%R_vni'] = ((data_vni['high_vni'].rolling(window=stoch_period).max() - data_vni['close_vni']) /
                (data_vni['high_vni'].rolling(window=stoch_period).max() - data_vni['low_vni'].rolling(window=stoch_period).min())) * -100

    # Tính toán CCI (Commodity Channel Index)
    cci_period = 20
    data_vni['typical_price_vni'] = (data_vni['high_vni'] + data_vni['low_vni'] + data_vni['close_vni']) / 3
    data_vni['cci_vni'] = CCIIndicator(high=data_vni['high_vni'], low=data_vni['low_vni'], close=data_vni['close_vni'], window=cci_period).cci()

    # Tính toán OBV (On Balance Volume)
    data_vni['obv_vni'] = OnBalanceVolumeIndicator(close=data_vni['close_vni'], volume=data_vni['volume_vni']).on_balance_volume()

    # Tính toán EMA ngắn hạn (12 ngày)
    data_vni['ema_12_vni'] = data_vni['close_vni'].ewm(span=12, adjust=False).mean()

    # Tính toán EMA dài hạn (26 ngày)
    data_vni['ema_26_vni'] = data_vni['close_vni'].ewm(span=26, adjust=False).mean()

    # Tính toán SMA trung hạn (20 ngày)
    data_vni['sma_20_vni'] = data_vni['close_vni'].rolling(window=20).mean()

    # Tính toán SMA dài hạn (50 ngày)
    data_vni['sma_50_vni'] = data_vni['close_vni'].rolling(window=50).mean()

    data_vni['hl_ratio_vni'] = data_vni['high_vni'] / (data_vni['low_vni'] + 1e-8)
    data_vni['co_ratio_vni'] = data_vni['close_vni'] / (data_vni['open_vni'] + 1e-8)
    data_vni['price_range_vni'] = (data_vni['high_vni'] - data_vni['low_vni']) / (data_vni['close_vni'] + 1e-8)

    if 'sma_20_vni' in data_vni.columns and 'sma_50_vni' in data_vni.columns:
        data_vni['sma_ratio_20_50_vni'] = data_vni['sma_20_vni'] / (data_vni['sma_50_vni'] + 1e-8)
    if 'ema_12_vni' in data_vni.columns and 'ema_26_vni' in data_vni.columns:
        data_vni['ema_ratio_12_26_vni'] = data_vni['ema_12_vni'] / (data_vni['ema_26_vni'] + 1e-8)

    if all(col in data_vni.columns for col in ['bb_bbh_vni', 'bb_bbl_vni', 'bb_bbm_vni']):
        data_vni['bb_width_vni'] = (data_vni['bb_bbh_vni'] - data_vni['bb_bbl_vni']) / (data_vni['bb_bbm_vni'] + 1e-8)
        data_vni['bb_position_vni'] = (data_vni['close_vni'] - data_vni['bb_bbl_vni']) / (data_vni['bb_bbh_vni'] - data_vni['bb_bbl_vni'] + 1e-8)

    if 'rsi_vni' in data_vni.columns:
        data_vni['rsi_overbought_vni'] = (data_vni['rsi_vni'] > 70).astype(int)
        data_vni['rsi_oversold_vni'] = (data_vni['rsi_vni'] < 30).astype(int)
        data_vni['rsi_neutral_vni'] = ((data_vni['rsi_vni'] >= 30) & (data_vni['rsi_vni'] <= 70)).astype(int)

    if all(col in data_vni.columns for col in ['macd_vni', 'signal_line_vni']):
        data_vni['macd_signal_diff_vni'] = data_vni['macd_vni'] - data_vni['signal_line_vni']
        data_vni['macd_bullish_vni'] = (data_vni['macd_vni'] > data_vni['signal_line_vni']).astype(int)

    for period in [5, 10]:
        if len(data_vni) > period:
            df[f'momentum_{period}_vni'] = data_vni['close_vni'].pct_change(period)

    
    # 1. Daily log return
    data_vni['log_return_vni'] = np.log(data_vni['close_vni'] / data_vni['close_vni'].shift(1))

    # 2. Rolling volatility (biến động trượt)
    for window in [5, 10, 20, 30]:
        data_vni[f'volatility_{window}d_vni'] = data_vni['log_return_vni'].rolling(window=window).std()

    # 3. Rolling mean log return
    for window in [5, 10, 20, 30]:
        data_vni[f'mean_log_return_{window}d_vni'] = data_vni['log_return_vni'].rolling(window=window).mean()

    # 4. Sharpe-like ratio (mean return / volatility)
    for window in [5, 10, 20, 30]:
        mean_col_vni = f'mean_log_return_{window}d_vni'
        vol_col_vni = f'volatility_{window}d_vni'
        data_vni[f'sharpe_like_{window}d_vni'] = data_vni[mean_col_vni] / (data_vni[vol_col_vni] + 1e-9)

    # 5. Directional Feature - chuỗi ngày tăng liên tiếp
    data_vni['up_streak_vni'] = (data_vni['log_return_vni'] > 0).astype(int)
    data_vni['up_streak_vni'] = data_vni['up_streak_vni'] * (data_vni['up_streak_vni'].groupby((data_vni['up_streak_vni'] != data_vni['up_streak_vni'].shift()).cumsum()).cumcount() + 1)
    data_vni['up_streak_vni'] = data_vni['up_streak_vni'].where(data_vni['log_return_vni'] > 0, 0)

    # 6. Tỷ lệ ngày log return dương trong 20 ngày gần nhất
    data_vni['pos_log_return_ratio_20d_vni'] = data_vni['log_return_vni'].rolling(window=20).apply(lambda x: np.mean(x > 0), raw=True)

    # 7. Z-score của log return hiện tại
    for window in [5, 10, 20, 30]:
        mean_col_vni = f'mean_log_return_{window}d_vni'
        vol_col_vni = f'volatility_{window}d_vni'
        data_vni[f'z_score_{window}d_vni'] = (data_vni['log_return_vni'] - data_vni[mean_col_vni]) / (data_vni[vol_col_vni] + 1e-9)



    # Tính Annual Return (lợi nhuận hàng năm)
    data_vni['annual_return_vni'] = data_vni['close_vni'] / data_vni['close_vni'].shift(252) - 1  # 252 ngày giao dịch trong năm

    # Tính Volatility (Độ biến động) hàng năm (Standard Deviation of Returns)
    data_vni['daily_return_vni'] = data_vni['close_vni'].pct_change()  # Tỷ suất lợi nhuận hàng ngày
    data_vni['annual_volatility_vni'] = data_vni['daily_return_vni'].rolling(window=252).std() * (252 ** 0.5)  # Độ lệch chuẩn hàng năm (tính từ tỷ suất lợi nhuận hàng ngày)

    risk_free_rate = 0.03  # tương đương 3%/năm
    # Tính Sharpe ratio: (Rp - Rf) / Volatility
    data_vni['sharpe_ratio_vni'] = (data_vni['annual_return_vni'] - risk_free_rate) / data_vni['annual_volatility_vni']


    data_vni['time'] = pd.to_datetime(data_vni['time']).dt.date


    # Xứ lý với VN30 =============================================================================

    data_vn30 = load_stock('VN30', folder_path)
    data_vn30 = data_vn30.drop(columns=['ticket'])
    data_vn30.columns = ['time','open_vn30', 'high_vn30', 'low_vn30', 'close_vn30', 'volume_vn30']


    # Tính toán RSI
    rsi_period = 14
    data_vn30['rsi_vn30'] = RSIIndicator(data_vn30['close_vn30'], window=rsi_period).rsi()
    # Tính toán RSI-base-MA
    ma_period = 9
    data_vn30['rsi_base_ma_vn30'] = data_vn30['rsi_vn30'].rolling(window=ma_period).mean()
    data_vn30['rsi_rsi_base_ma_ratio_vn30'] = data_vn30['rsi_vn30'] / data_vn30['rsi_base_ma_vn30']

    # Tính toán khối lượng trung bình
    volume_ma_period = 20  # Ví dụ: khối lượng trung bình 20 ngày
    data_vn30['volume_ma_vn30'] = data_vn30['volume_vn30'].rolling(window=volume_ma_period).mean()
    # Tính tỷ lệ khối lượng hiện tại / khối lượng trung bình
    data_vn30['volume_to_volume_ma_ratio_vn30'] = data_vn30['volume_vn30'] / data_vn30['volume_ma_vn30']

    # Bollinger Bands
    indicator_bb = BollingerBands(close=data_vn30['close_vn30'], window=20, window_dev=2)
    data_vn30['bb_bbm_vn30'] = indicator_bb.bollinger_mavg()
    data_vn30['bb_bbh_vn30'] = indicator_bb.bollinger_hband()
    data_vn30['bb_bbl_vn30'] = indicator_bb.bollinger_lband()
    data_vn30['bb_bbp_vn30'] = indicator_bb.bollinger_pband()

    data_vn30['bb_bbh_bb_bbl_ratio_vn30'] = data_vn30['bb_bbh_vn30'] / data_vn30['bb_bbl_vn30']

    # Tính toán ROC
    roc_period = 9  # Chu kỳ 9 ngày, bạn có thể thay đổi tùy ý
    # data_vn30['roc_vn30'] = ((data_vn30['close_vn30'] - data_vn30['close_vn30'].shift(roc_period)) / data_vn30['close_vn30'].shift(roc_period)) * 100
    data_vn30['roc_1_vn30'] = ((data_vn30['close_vn30'] - data_vn30['close_vn30'].shift(1)) / data_vn30['close_vn30'].shift(1)) * 100
    data_vn30['roc_5_vn30'] = ((data_vn30['close_vn30'] - data_vn30['close_vn30'].shift(5)) / data_vn30['close_vn30'].shift(5)) * 100
    data_vn30['roc_9_vn30'] = ((data_vn30['close_vn30'] - data_vn30['close_vn30'].shift(9)) / data_vn30['close_vn30'].shift(9)) * 100

    # Tính toán %K (Stochastic Oscillator)
    stoch_period = 14
    data_vn30['%K_vn30'] = ((data_vn30['close_vn30'] - data_vn30['low_vn30'].rolling(window=stoch_period).min()) /
                (data_vn30['high_vn30'].rolling(window=stoch_period).max() - data_vn30['low_vn30'].rolling(window=stoch_period).min())) * 100

    # Tính toán %R (Williams %R)
    data_vn30['%R_vn30'] = ((data_vn30['high_vn30'].rolling(window=stoch_period).max() - data_vn30['close_vn30']) /
                (data_vn30['high_vn30'].rolling(window=stoch_period).max() - data_vn30['low_vn30'].rolling(window=stoch_period).min())) * -100

    # Tính toán CCI (Commodity Channel Index)
    cci_period = 20
    data_vn30['typical_price_vn30'] = (data_vn30['high_vn30'] + data_vn30['low_vn30'] + data_vn30['close_vn30']) / 3
    data_vn30['cci_vn30'] = CCIIndicator(high=data_vn30['high_vn30'], low=data_vn30['low_vn30'], close=data_vn30['close_vn30'], window=cci_period).cci()

    # Tính toán OBV (On Balance Volume)
    data_vn30['obv_vn30'] = OnBalanceVolumeIndicator(close=data_vn30['close_vn30'], volume=data_vn30['volume_vn30']).on_balance_volume()

    # Tính toán EMA ngắn hạn (12 ngày)
    data_vn30['ema_12_vn30'] = data_vn30['close_vn30'].ewm(span=12, adjust=False).mean()

    # Tính toán EMA dài hạn (26 ngày)
    data_vn30['ema_26_vn30'] = data_vn30['close_vn30'].ewm(span=26, adjust=False).mean()

    # Tính toán SMA trung hạn (20 ngày)
    data_vn30['sma_20_vn30'] = data_vn30['close_vn30'].rolling(window=20).mean()

    # Tính toán SMA dài hạn (50 ngày)
    data_vn30['sma_50_vn30'] = data_vn30['close_vn30'].rolling(window=50).mean()

    data_vn30['hl_ratio_vn30'] = data_vn30['high_vn30'] / (data_vn30['low_vn30'] + 1e-8)
    data_vn30['co_ratio_vn30'] = data_vn30['close_vn30'] / (data_vn30['open_vn30'] + 1e-8)
    data_vn30['price_range_vn30'] = (data_vn30['high_vn30'] - data_vn30['low_vn30']) / (data_vn30['close_vn30'] + 1e-8)

    if 'sma_20_vn30' in data_vn30.columns and 'sma_50_vn30' in data_vn30.columns:
        data_vn30['sma_ratio_20_50_vn30'] = data_vn30['sma_20_vn30'] / (data_vn30['sma_50_vn30'] + 1e-8)
    if 'ema_12_vn30' in data_vn30.columns and 'ema_26_vn30' in data_vn30.columns:
        data_vn30['ema_ratio_12_26_vn30'] = data_vn30['ema_12_vn30'] / (data_vn30['ema_26_vn30'] + 1e-8)

    if all(col in data_vn30.columns for col in ['bb_bbh_vn30', 'bb_bbl_vn30', 'bb_bbm_vn30']):
        data_vn30['bb_width_vn30'] = (data_vn30['bb_bbh_vn30'] - data_vn30['bb_bbl_vn30']) / (data_vn30['bb_bbm_vn30'] + 1e-8)
        data_vn30['bb_position_vn30'] = (data_vn30['close_vn30'] - data_vn30['bb_bbl_vn30']) / (data_vn30['bb_bbh_vn30'] - data_vn30['bb_bbl_vn30'] + 1e-8)

    if 'rsi_vn30' in data_vn30.columns:
        data_vn30['rsi_overbought_vn30'] = (data_vn30['rsi_vn30'] > 70).astype(int)
        data_vn30['rsi_oversold_vn30'] = (data_vn30['rsi_vn30'] < 30).astype(int)
        data_vn30['rsi_neutral_vn30'] = ((data_vn30['rsi_vn30'] >= 30) & (data_vn30['rsi_vn30'] <= 70)).astype(int)

    if all(col in data_vn30.columns for col in ['macd_vn30', 'signal_line_vn30']):
        data_vn30['macd_signal_diff_vn30'] = data_vn30['macd_vn30'] - data_vn30['signal_line_vn30']
        data_vn30['macd_bullish_vn30'] = (data_vn30['macd_vn30'] > data_vn30['signal_line_vn30']).astype(int)

    for period in [5, 10]:
        if len(data_vn30) > period:
            df[f'momentum_{period}_vn30'] = data_vn30['close_vn30'].pct_change(period)


    # 1. Daily log return
    data_vn30['log_return_vn30'] = np.log(data_vn30['close_vn30'] / data_vn30['close_vn30'].shift(1))

    # 2. Rolling volatility (biến động trượt)
    for window in [5, 10, 20, 30]:
        data_vn30[f'volatility_{window}d_vn30'] = data_vn30['log_return_vn30'].rolling(window=window).std()

    # 3. Rolling mean log return
    for window in [5, 10, 20, 30]:
        data_vn30[f'mean_log_return_{window}d_vn30'] = data_vn30['log_return_vn30'].rolling(window=window).mean()

    # 4. Sharpe-like ratio (mean return / volatility)
    for window in [5, 10, 20, 30]:
        mean_col_vn30 = f'mean_log_return_{window}d_vn30'
        vol_col_vn30 = f'volatility_{window}d_vn30'
        data_vn30[f'sharpe_like_{window}d_vn30'] = data_vn30[mean_col_vn30] / (data_vn30[vol_col_vn30] + 1e-9)

    # 5. Directional Feature - chuỗi ngày tăng liên tiếp
    data_vn30['up_streak_vn30'] = (data_vn30['log_return_vn30'] > 0).astype(int)
    data_vn30['up_streak_vn30'] = data_vn30['up_streak_vn30'] * (data_vn30['up_streak_vn30'].groupby((data_vn30['up_streak_vn30'] != data_vn30['up_streak_vn30'].shift()).cumsum()).cumcount() + 1)
    data_vn30['up_streak_vn30'] = data_vn30['up_streak_vn30'].where(data_vn30['log_return_vn30'] > 0, 0)

    # 6. Tỷ lệ ngày log return dương trong 20 ngày gần nhất
    data_vn30['pos_log_return_ratio_20d_vn30'] = data_vn30['log_return_vn30'].rolling(window=20).apply(lambda x: np.mean(x > 0), raw=True)

    # 7. Z-score của log return hiện tại
    for window in [5, 10, 20, 30]:
        mean_col_vn30 = f'mean_log_return_{window}d_vn30'
        vol_col_vn30 = f'volatility_{window}d_vn30'
        data_vn30[f'z_score_{window}d_vn30'] = (data_vn30['log_return_vn30'] - data_vn30[mean_col_vn30]) / (data_vn30[vol_col_vn30] + 1e-9)


    # Tính Annual Return (lợi nhuận hàng năm)
    data_vn30['annual_return_vn30'] = data_vn30['close_vn30'] / data_vn30['close_vn30'].shift(252) - 1  # 252 ngày giao dịch trong năm

    # Tính Volatility (Độ biến động) hàng năm (Standard Deviation of Returns)
    data_vn30['daily_return_vn30'] = data_vn30['close_vn30'].pct_change()  # Tỷ suất lợi nhuận hàng ngày
    data_vn30['annual_volatility_vn30'] = data_vn30['daily_return_vn30'].rolling(window=252).std() * (252 ** 0.5)  # Độ lệch chuẩn hàng năm (tính từ tỷ suất lợi nhuận hàng ngày)

    risk_free_rate = 0.03  # tương đương 3%/năm
    # Tính Sharpe ratio: (Rp - Rf) / Volatility
    data_vn30['sharpe_ratio_vn30'] = (data_vn30['annual_return_vn30'] - risk_free_rate) / data_vn30['annual_volatility_vn30']


    data_vn30['time'] = pd.to_datetime(data_vn30['time']).dt.date



    # merge
    df['time'] = pd.to_datetime(df['time']).dt.date
    df = pd.merge(df, data_vni, on='time')
    df = pd.merge(df, data_vn30, on='time')


     # Tính tỷ lệ thay đổi giá
    threshold=0.01
    df['change'] = (df['close'].shift(-1) - df['close']) / df['close']

    # Gán nhãn
    df['target'] = 1  # Hold mặc định
    df.loc[df['change'] > threshold, 'target'] = 2   # Buy
    df.loc[df['change'] < -threshold, 'target'] = 0  # Sell

    if drop_na:
        df.dropna(inplace=True)

    return df

In [19]:
def add_slope_features(df, feature_base_names, n=8):
    """
    Với mỗi dòng trong df, tính hệ số gốc (slope) của đường hồi quy tuyến tính theo thời gian
    cho từng feature trong danh sách feature_base_names dựa trên các giá trị 8 quý gần nhất.

    Args:
        df (pd.DataFrame): DataFrame chứa các cột dạng 'feature_d_1' đến 'feature_d_n'.
        feature_base_names (list): Danh sách tên feature cơ bản (string).
        n (int): Số quý gần nhất để tính trend (mặc định 8).

    Returns:
        pd.DataFrame: DataFrame đã thêm các cột hệ số gốc tương ứng.
    """
    for feature in feature_base_names:
        col_name = f"coefficient_{feature}"
        if col_name not in df.columns:
            df[col_name] = np.nan

    # Duyệt từng hàng
    for index, row in df.iterrows():
        for feature in feature_base_names:
            y_values = []
            for i in range(n, 0, -1):  # d_8, ..., d_1
                val = row.get(f"{feature}_d_{i}", np.nan)
                y_values.append(val)

            y_values = np.array(y_values, dtype=float)

            # Cần ít nhất 2 điểm hợp lệ để fit mô hình
            if np.isnan(y_values).sum() > (n - 2):
                coef = np.nan
            else:
                X = np.arange(n).reshape(-1, 1)
                mask = ~np.isnan(y_values)
                model = LinearRegression()
                model.fit(X[mask], y_values[mask])
                coef = model.coef_[0]

            df.at[index, f"coefficient_{feature}"] = coef

    return df

In [20]:
def fn_load_and_process_data(symbol, drop_na=True, folder_path = ''):
  df = load_and_process_data(symbol, drop_na, folder_path)
  feature_base_names = ['P/B','P/E','P/S','P/Cash Flow','EPS (VND)','BVPS (VND)','ROE (%)','ROA (%)']
  df = add_slope_features(df, feature_base_names)

  df.rename(columns={
            'P/B_Previous_Quarter': 'p/b_previous_quarter',
            'P/B_change_rate': 'p/b_change_rate',
            'P/B_change_rate_flag': 'p/b_change_rate_flag',
            'P/E_Previous_Quarter': 'p/e_previous_quarter',
            'P/E_change_rate': 'p/e_change_rate',
            'P/E_change_rate_flag':'p/e_change_rate_flag',
            'P/S_Previous_Quarter': 'p/s_previous_quarter',
            'P/S_change_rate': 'p/s_change_rate',
            'P/S_change_rate_flag': 'p/s_change_rate_flag',
            'P/Cash Flow_Previous_Quarter': 'p/cash_flow_previous_quarter',
            'P/Cash Flow_change_rate': 'p/cash_flow_change_rate',
            'P/Cash Flow_change_rate_flag' : 'p/cash_flow_change_rate_flag',
            'EPS (VND)_Previous_Quarter': 'eps_previous_quarter',
            'EPS (VND)_change_rate': 'eps_change_rate',
            'EPS (VND)_change_rate_flag': 'eps_change_rate_flag',
            'BVPS (VND)_Previous_Quarter': 'bvps_previous_quarter',
            'BVPS (VND)_change_rate' : 'bvps_change_rate',
            'BVPS (VND)_change_rate_flag': 'bvps_change_rate_flag',
            'ROE (%)_Previous_Quarter': 'roe_previous_quarter',
            'ROE (%)_change_rate': 'roe_change_rate',
            'ROE (%)_change_rate_flag': 'roe_change_rate_flag',
            'ROA (%)_Previous_Quarter': 'roa_previous_quarter',
            'ROA (%)_change_rate': 'roa_change_rate',
            'ROA (%)_change_rate_flag': 'roa_change_rate_flag',
            'coefficient_P/B': 'coefficient_p/b',
            'coefficient_P/E': 'coefficient_p/e',
            'coefficient_P/S': 'coefficient_p/s',
            'coefficient_P/Cash Flow': 'coefficient_p/cash_flow',
            'coefficient_EPS (VND)': 'coefficient_eps',
            'coefficient_BVPS (VND)': 'coefficient_bvps',
            'coefficient_ROE (%)': 'coefficient_roe',
            'coefficient_ROA (%)': 'coefficient_roa'


        }, inplace=True)  
  return df

In [17]:
df_vhm_process = fn_load_and_process_data("VHM", folder_path= rf'D:\thacsi\TAILIEULUANVAN\code\PredictStock_TA_FA_SA\TA_FA\data\v2\data_train')

✅ Đã load dữ liệu cho mã: VHM
✅ Đã load dữ liệu cho mã: VNINDEX
✅ Đã load dữ liệu cho mã: VN30


In [ ]:
df_vhm_process

Index(['time', 'open', 'high', 'low', 'close', 'volume',
       'P/B_Previous_Quarter', 'P/B_Same_Period_Last_Year', 'P/B_d_1',
       'P/B_d_2',
       ...
       'change', 'target', 'coefficient_P/B', 'coefficient_P/E',
       'coefficient_P/S', 'coefficient_P/Cash Flow', 'coefficient_EPS (VND)',
       'coefficient_BVPS (VND)', 'coefficient_ROE (%)', 'coefficient_ROA (%)'],
      dtype='object', length=224)

In [19]:
df_vhm_process.to_excel(r"D:\output.xlsx", index=False)

In [21]:
def compute_sentiment_norm(sentiment_df):
    # Xác định các cột khía cạnh cảm xúc (giả sử các cột này có tên như dưới)
    sentiment_columns = [
        'Reputation', 'Company Communication', 'Appointment', 'Financial', 'Regulatory',
        'Sales', 'M&A', 'Legal', 'Dividend Policy', 'Risks', 'Rumors', 'Strategy',
        'Options', 'IPO', 'Signal', 'Coverage', 'Fundamentals', 'Insider Activity',
        'Price Action', 'Buyside', 'Technical Analysis', 'Trade', 'Central Banks',
        'Currency', 'Conditions', 'Market', 'Volatility', 'Investor Sentiment', 'Retail Investor Behavior',
        'Speculation', 'Domestic Institutional Behavior', 'Foreign Institutional Behavior', 'Black Swan Event',
    ]

    # Đảm bảo các cột này đều tồn tại trong DataFrame
    existing_columns = [col for col in sentiment_columns if col in sentiment_df.columns]

    # Thay NaN bằng 0 nếu chưa làm
    sentiment_df[existing_columns] = sentiment_df[existing_columns].fillna(0)

    # Tính Euclidean norm cho từng hàng
    sentiment_df['euclidean norm'] = np.linalg.norm(sentiment_df[existing_columns].values, axis=1)

    return sentiment_df

In [22]:
def to_snake_case(name: str) -> str:
    return name.strip().lower().replace(' ', '_')

In [27]:
def apply_sentiment_for_ta_fa(symbol, ta_fa_data_folder_path, sentiment_data_folder_path, destination_folder_path, drop_na=True):
    ta_fa_df = fn_load_and_process_data(symbol, drop_na, ta_fa_data_folder_path)
    ta_fa_df.reset_index(drop=True, inplace=True)
    # sentiment_df = pd.read_excel(sentiment_data_folder_path + "/" + symbol + ".xlsx")
    df_sentiment_cafef = pd.read_excel(os.path.join(sentiment_data_folder_path, "cafef", "v2", "test_data", f"{symbol}.xlsx" ))
    df_sentiment_vietnamnet_vnxpress_tuoitre = pd.read_excel(os.path.join(sentiment_data_folder_path, "vnexpress_vietnamnet_tuoitre", "v2", "test_data", f"{symbol}.xlsx" ))
    df_sentiment_official_statement = pd.read_excel(os.path.join(sentiment_data_folder_path, "official_statement", "v2", "test_data", f"{symbol}.xlsx" ))
    df_sentiment_official_statement = df_sentiment_official_statement[[
        'ticker','time','tittle','url','Content',
        'Reputation', 'Company Communication', 'Appointment', 'Financial', 'Regulatory',
        'Sales', 'M&A', 'Legal', 'Dividend Policy', 'Risks', 'Rumors', 'Strategy',
        'Options', 'IPO', 'Signal', 'Coverage', 'Fundamentals', 'Insider Activity',
        'Price Action', 'Buyside', 'Technical Analysis', 'Trade', 'Central Banks',
        'Currency', 'Conditions', 'Market', 'Volatility', 'Investor Sentiment', 'Retail Investor Behavior',
        'Speculation', 'Domestic Institutional Behavior', 'Foreign Institutional Behavior', 'Black Swan Event',
    ]]

    sentiment_df = pd.concat([
        df_sentiment_cafef,
        df_sentiment_vietnamnet_vnxpress_tuoitre,
        df_sentiment_official_statement
    ], ignore_index=True)
    print("Đã ghép sentiment cafef, vietnamnet, vnexpress, tuổi trẻ, official statement")
    # Xử lý thiếu và chuẩn hóa
    sentiment_df.fillna(0, inplace=True)
    sentiment_df = compute_sentiment_norm(sentiment_df)
    # sentiment_df.to_excel(r"D:\sentiment_df.xlsx", index=False)

    # Định dạng thời gian
    sentiment_df['time'] = pd.to_datetime(sentiment_df['time'], dayfirst=True, errors='coerce')
    ta_fa_df['time'] = pd.to_datetime(ta_fa_df['time'], dayfirst=True)

    # Danh sách cột cảm xúc
    sentiment_columns = [
        'Reputation', 'Company Communication', 'Appointment', 'Financial', 'Regulatory',
        'Sales', 'M&A', 'Legal', 'Dividend Policy', 'Risks', 'Rumors', 'Strategy',
        'Options', 'IPO', 'Signal', 'Coverage', 'Fundamentals', 'Insider Activity',
        'Price Action', 'Buyside', 'Technical Analysis', 'Trade', 'Central Banks',
        'Currency', 'Conditions', 'Market', 'Volatility', 'Investor Sentiment', 'Retail Investor Behavior',
        'Speculation', 'Domestic Institutional Behavior', 'Foreign Institutional Behavior', 'Black Swan Event',
    ]

    # Thêm các cột cảm xúc vào `ta_fa_df`, mặc định là 0
    for col in sentiment_columns:
        ta_fa_df[col] = 0.0

    for i in range(len(ta_fa_df) - 1):
        current_date = ta_fa_df.at[i, 'time']
        next_trading_date = ta_fa_df.at[i + 1, 'time']

        from_time = datetime.combine(current_date, datetime.min.time()) + timedelta(hours=14, minutes=45)
        to_time = datetime.combine(next_trading_date, datetime.min.time()) + timedelta(hours=14, minutes=45)

        mask = (sentiment_df['time'] >= from_time) & (sentiment_df['time'] < to_time)
        news_in_range = sentiment_df[mask]

        print(f"\n📅 Ngày đang xét: {current_date.date()}")
        print(f"📅 Ngày giao dịch tiếp theo: {next_trading_date.date()}")
        print(f"📰 Các tin tức từ {from_time} đến {to_time} sẽ ảnh hưởng đến nhãn tại ngày {current_date.date()}:")

        if news_in_range.empty:
            print(" - Không có tin tức ảnh hưởng.")
            print("📊 Các khía cạnh cảm xúc (mặc định 0):")
            continue

        max_norm_idx = news_in_range['euclidean norm'].idxmax()
        max_news = news_in_range.loc[max_norm_idx]

        for idx, row in news_in_range.iterrows():
            title = row.get('tittle', '[Không có tiêu đề]')
            time_str = row['time']
            print(f" - {time_str}: {title}")
            for col in sentiment_columns:
                    print(f"   - {col}: {row[col]}")
            if idx == max_norm_idx:
                print("  🔍 Đây là tin có euclidean norm cao nhất.")
                print("  📊 Các khía cạnh cảm xúc:")
                for col in sentiment_columns:
                    print(f"   - {col}: {row[col]}")

        # Nếu muốn tính tổng hợp nhiều tin trong ngày
        ta_fa_df.at[i, 'num_sa_news'] = len(news_in_range)
        ta_fa_df.at[i, 'mean_sentiment_norm'] = news_in_range['euclidean norm'].mean()
        ta_fa_df.at[i, 'max_sentiment_norm'] = news_in_range['euclidean norm'].max()
        ta_fa_df.at[i, 'std_sentiment_score'] = news_in_range[sentiment_columns].std().mean()

        # Tính tổng các cảm xúc tích cực / tiêu cực
        pos_sum = news_in_range[sentiment_columns].applymap(lambda x: x if x > 0 else 0).sum().sum()
        neg_sum = news_in_range[sentiment_columns].applymap(lambda x: x if x < 0 else 0).sum().sum()

        ta_fa_df.at[i, 'sum_positive_sa'] = pos_sum
        ta_fa_df.at[i, 'sum_negative_sa'] = neg_sum

        # ➕ Tính khoảng cách đến 14:45 hôm đó (âm nếu tin xảy ra trước giờ đóng cửa)
        news_time = max_news['time']
        cutoff_time = datetime.combine(current_date, datetime.min.time()) + timedelta(hours=14, minutes=45)
        time_distance_minutes = (cutoff_time - news_time).total_seconds() / 60.0
        ta_fa_df.at[i, 'time_distance_from_sa_to_close_minutes'] = time_distance_minutes

        # Gán các giá trị cảm xúc vào ta_fa_df tại dòng i
        for col in sentiment_columns:
            ta_fa_df.at[i, col] = max_news[col]
    
    # Tạo các cột hiệu ứng chậm từ cảm xúc hôm trước

    for col in sentiment_columns:
        ta_fa_df[f"{to_snake_case(col)}_p1d"] = ta_fa_df[col].shift(1)

    meta_cols = ['num_sa_news', 'mean_sentiment_norm', 'max_sentiment_norm', 'std_sentiment_score', 'sum_positive_sa', 'sum_negative_sa', 'time_distance_from_sa_to_close_minutes']
    for col in meta_cols:
        ta_fa_df[f"{col}_p1d"] = ta_fa_df[col].shift(1)
    ta_fa_df.fillna(0, inplace=True)

    # Lưu ra file đích
    os.makedirs(destination_folder_path, exist_ok=True)
    destination_file = f"{destination_folder_path}/{symbol}.xlsx"
    with pd.ExcelWriter(destination_file, engine='openpyxl', mode='w') as writer:
      ta_fa_df.to_excel(writer, sheet_name='Sheet1', index=False)
    print("Đã lưu " +str(destination_file))

    return ta_fa_df


In [23]:
apply_sentiment_for_ta_fa("VHM", ta_fa_data_folder_path= r'D:\thacsi\TAILIEULUANVAN\code\PredictStock_TA_FA_SA\TA_FA\data\v2\data_test', sentiment_data_folder_path= r'D:\thacsi\TAILIEULUANVAN\code\PredictStock_TA_FA_SA\SA\data\v2\sentiment_score_data', destination_folder_path=r"D:\thacsi\TAILIEULUANVAN\code\PredictStock_TA_FA_SA\TA_FA_SA\data\v2\stock_trend\test_data" )

✅ Đã load dữ liệu cho mã: VHM
✅ Đã load dữ liệu cho mã: VNINDEX
✅ Đã load dữ liệu cho mã: VN30

📅 Ngày đang xét: 2024-01-05
📅 Ngày giao dịch tiếp theo: 2024-01-08
📰 Các tin tức từ 2024-01-05 14:45:00 đến 2024-01-08 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-01-05:
 - Không có tin tức ảnh hưởng.
📊 Các khía cạnh cảm xúc (mặc định 0):

📅 Ngày đang xét: 2024-01-08
📅 Ngày giao dịch tiếp theo: 2024-01-09
📰 Các tin tức từ 2024-01-08 14:45:00 đến 2024-01-09 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-01-08:
 - 2024-01-09 12:42:00: Vinhomes tuyển môi giới bất động sản quy mô lớn để tự bán hàng
   - Reputation: 0.5
   - Appointment: 0.0
   - Financial: 0.3
   - Regulatory: 0.0
   - Sales: 0.6
   - M&A: 0.0
   - Legal: 0.0
   - Risks: 0.2
   - Rumors: 0.0
   - Strategy: 0.7
   - Options: 0.0
   - IPO: 0.0
   - Signal: 0.5
   - Coverage: 0.0
   - Fundamentals: 0.3
   - Buyside: 0.0
   - Trade: 0.0
   - Currency: 0.0
   - Conditions: 0.0
   - Market: 0.4
   - Volatility: 0.2
  🔍 Đây là tin có eu

time   open   high    low  close   volume  P/B_Previous_Quarter  \
0   2024-01-05  43.45  43.55  43.05  43.10  4510634              1.080688   
1   2024-01-08  43.20  43.85  42.90  43.35  6216748              1.080688   
2   2024-01-09  43.15  43.30  42.65  43.00  6379398              1.080688   
3   2024-01-10  43.00  43.00  42.10  42.70  6792763              1.080688   
4   2024-01-11  42.50  43.05  42.00  42.00  6971310              1.080688   
..         ...    ...    ...    ...    ...      ...                   ...   
241 2024-12-24  40.50  40.60  40.10  40.35  3214900              0.820944   
242 2024-12-25  40.50  40.75  40.35  40.60  3559700              0.820944   
243 2024-12-26  40.75  41.30  40.65  40.65  3690900              0.820944   
244 2024-12-27  40.80  41.05  40.35  40.35  2847200              0.820944   
245 2024-12-30  40.45  40.60  40.30  40.30  2516300              0.820944   

     P/B_Same_Period_Last_Year   P/B_d_1   P/B_d_2  ...  IPO  Signal  \
0                     1.499301  1.080688  1.012768  ...  0.0     0.0   
1                     1.499301  1.080688  1.012768  ...  0.0     0.5   
2                     1.499301  1.080688  1.012768  ...  0.0     0.0   
3                     1.499301  1.080688  1.012768  ...  0.0     0.0   
4                     1.499301  1.080688  1.012768  ...  0.0     0.0   
..                         ...       ...       ...  ...  ...     ...   
241                   1.012768  0.820944  1.027068  ...  0.0     0.0   
242                   1.012768  0.820944  1.027068  ...  0.0     0.4   
243                   1.012768  0.820944  1.027068  ...  0.0     0.0   
244                   1.012768  0.820944  1.027068  ...  0.0     0.3   
245                   1.012768  0.820944  1.027068  ...  0.0     0.0   

     Coverage  Fundamentals  Buyside  Trade  Currency  Conditions  Market  \
0         0.0           0.0      0.0    0.0       0.0         0.0     0.0   
1         0.0           0.3      0.0    0.0       0.0         0.0     0.4   
2         0.0           0.0      0.0    0.0       0.0         0.0     0.0   
3         0.0           0.0      0.0    0.0       0.0         0.0     0.0   
4         0.0           0.0      0.0    0.0       0.0         0.0     0.0   
..        ...           ...      ...    ...       ...         ...     ...   
241       0.0           0.0      0.0    0.0       0.0         0.0     0.0   
242       0.0           0.3      0.0    0.0       0.1         0.0     0.5   
243       0.0           0.0      0.0    0.0       0.0         0.0     0.0   
244       0.0           0.4      0.0    0.0       0.0         0.0     0.3   
245       0.0           0.0      0.0    0.0       0.0         0.0     0.0   

     Volatility  
0           0.0  
1           0.2  
2           0.0  
3           0.0  
4           0.0  
..          ...  
241         0.0  
242         0.3  
243         0.0  
244         0.1  
245         0.0  

[246 rows x 245 columns]

In [28]:
def apply_sentiment_for_ta_fa_vn30(tickers):
  ta_fa_data_folder_path = r'D:\thacsi\TAILIEULUANVAN\code\PredictStock_TA_FA_SA\TA_FA\data\v2\data_test'
  sentiment_data_folder_path = r'D:\thacsi\TAILIEULUANVAN\code\PredictStock_TA_FA_SA\SA\data\v2\sentiment_score_data'
  destination_folder_path = r"D:\thacsi\TAILIEULUANVAN\code\PredictStock_TA_FA_SA\TA_FA_SA\data\v6\stock_trend\test_data"
  for ticker in tickers:
    print(f"Đang xử lý {ticker}")
    apply_sentiment_for_ta_fa(ticker, ta_fa_data_folder_path, sentiment_data_folder_path, destination_folder_path)
    print(f"Đã xử lý xong {ticker}")


In [29]:
tickers = ['ACB','BCM', 'BID','BVH','CTG','FPT','GAS','GVR','HDB','HPG','LPB','MBB','MSN','MWG','PLX','SAB','SHB','SSB','SSI','STB','TCB','TPB','VCB','VHM','VIB','VIC','VJC','VNM','VPB','VRE']
# tickers = ['ACB']
apply_sentiment_for_ta_fa_vn30(tickers)

Đang xử lý ACB
✅ Đã load dữ liệu cho mã: ACB
✅ Đã load dữ liệu cho mã: VNINDEX
✅ Đã load dữ liệu cho mã: VN30
Đã ghép sentiment cafef, vietnamnet, vnexpress, tuổi trẻ, official statement

📅 Ngày đang xét: 2024-01-05
📅 Ngày giao dịch tiếp theo: 2024-01-08
📰 Các tin tức từ 2024-01-05 14:45:00 đến 2024-01-08 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-01-05:
 - Không có tin tức ảnh hưởng.
📊 Các khía cạnh cảm xúc (mặc định 0):

📅 Ngày đang xét: 2024-01-08
📅 Ngày giao dịch tiếp theo: 2024-01-09
📰 Các tin tức từ 2024-01-08 14:45:00 đến 2024-01-09 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-01-08:
 - Không có tin tức ảnh hưởng.
📊 Các khía cạnh cảm xúc (mặc định 0):

📅 Ngày đang xét: 2024-01-09
📅 Ngày giao dịch tiếp theo: 2024-01-10
📰 Các tin tức từ 2024-01-09 14:45:00 đến 2024-01-10 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-01-09:
 - Không có tin tức ảnh hưởng.
📊 Các khía cạnh cảm xúc (mặc định 0):

📅 Ngày đang xét: 2024-01-10
📅 Ngày giao dịch tiếp theo: 2024-01-11
📰 Các tin tức từ 2024-

DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map inst


📅 Ngày đang xét: 2024-04-02
📅 Ngày giao dịch tiếp theo: 2024-04-03
📰 Các tin tức từ 2024-04-02 14:45:00 đến 2024-04-03 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-04-02:
 - Không có tin tức ảnh hưởng.
📊 Các khía cạnh cảm xúc (mặc định 0):

📅 Ngày đang xét: 2024-04-03
📅 Ngày giao dịch tiếp theo: 2024-04-04
📰 Các tin tức từ 2024-04-03 14:45:00 đến 2024-04-04 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-04-03:
 - 2024-04-04 11:36:00: Chủ tịch ACB Trần Hùng Huy: KQKD của ACB quý I/2024 đạt khoảng 4.900 tỷ đồng, tín dụng tăng trưởng cao hơn gấp đôi toàn ngành
   - Reputation: 0.5
   - Company Communication: 0.4
   - Appointment: 0.0
   - Financial: 0.3
   - Regulatory: 0.0
   - Sales: 0.0
   - M&A: 0
   - Legal: 0.0
   - Dividend Policy: 0.0
   - Risks: 0.1
   - Rumors: 0.0
   - Strategy: 0.2
   - Options: 0
   - IPO: 0.0
   - Signal: 0.2
   - Coverage: 0
   - Fundamentals: 0.3
   - Insider Activity: 0.0
   - Price Action: 0.0
   - Buyside: 0
   - Technical Analysis: 0.0
   - Trade: 0.0
 

DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map inst


📅 Ngày đang xét: 2024-07-23
📅 Ngày giao dịch tiếp theo: 2024-07-24
📰 Các tin tức từ 2024-07-23 14:45:00 đến 2024-07-24 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-07-23:
 - 2024-07-24 10:46:00: ACB tăng trưởng tín dụng gấp đôi bình quân ngành, dẫn đầu thị trường về mức độ hiệu quả trong 6 tháng đầu năm 2024
   - Reputation: 0.8
   - Company Communication: 0.7
   - Appointment: 0.0
   - Financial: 0.9
   - Regulatory: 0.5
   - Sales: 0.6
   - M&A: 0
   - Legal: 0.0
   - Dividend Policy: 0.0
   - Risks: 0.2
   - Rumors: 0.0
   - Strategy: 0.8
   - Options: 0
   - IPO: 0.0
   - Signal: 0.7
   - Coverage: 0
   - Fundamentals: 0.9
   - Insider Activity: 0.0
   - Price Action: 0.6
   - Buyside: 0
   - Technical Analysis: 0.0
   - Trade: 0.0
   - Central Banks: 0.0
   - Currency: 0.0
   - Conditions: 0.5
   - Market: 0.7
   - Volatility: 0.2
   - Investor Sentiment: 0.8
   - Retail Investor Behavior: 0.0
   - Speculation: 0
   - Domestic Institutional Behavior: 0.0
   - Foreign Institutiona

...


📅 Ngày đang xét: 2024-08-12
📅 Ngày giao dịch tiếp theo: 2024-08-13
📰 Các tin tức từ 2024-08-12 14:45:00 đến 2024-08-13 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-08-12:
 - 2024-08-13 10:50:00: Công bố 10 công ty bất động sản tư nhân nộp ngân sách Nhà nước lớn nhất Việt Nam
   - Reputation: 0.3
   - Company Communication: 0.0
   - Appointment: 0.0
   - Financial: 0.5
   - Regulatory: 0.0
   - Sales: 0.0
   - M&A: 0.0
   - Legal: 0.0
   - Dividend Policy: 0.0
   - Risks: 0.0
   - Rumors: 0.0
   - Strategy: 0.0
   - Options: 0
   - IPO: 0.0
   - Signal: 0.0
   - Coverage: 0.0
   - Fundamentals: 0.0
   - Insider Activity: 0.0
   - Price Action: 0.0
   - Buyside: 0.0
   - Technical Analysis: 0.0
   - Trade: 0.0
   - Central Banks: 0.0
   - Currency: 0.0
   - Conditions: 0.0
   - Market: 0.0
   - Volatility: 0.0
   - Investor Sentiment: 0.0
   - Retail Investor Behavior: 0.0
   - Speculation: 0.0
   - Domestic Institutional Behavior: 0.0
   - Foreign Institutional Behavior: 0.0
   - Black

DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.



📅 Ngày đang xét: 2024-09-18
📅 Ngày giao dịch tiếp theo: 2024-09-19
📰 Các tin tức từ 2024-09-18 14:45:00 đến 2024-09-19 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-09-18:
 - Không có tin tức ảnh hưởng.
📊 Các khía cạnh cảm xúc (mặc định 0):

📅 Ngày đang xét: 2024-09-19
📅 Ngày giao dịch tiếp theo: 2024-09-20
📰 Các tin tức từ 2024-09-19 14:45:00 đến 2024-09-20 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-09-19:
 - Không có tin tức ảnh hưởng.
📊 Các khía cạnh cảm xúc (mặc định 0):

📅 Ngày đang xét: 2024-09-20
📅 Ngày giao dịch tiếp theo: 2024-09-23
📰 Các tin tức từ 2024-09-20 14:45:00 đến 2024-09-23 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-09-20:
 - Không có tin tức ảnh hưởng.
📊 Các khía cạnh cảm xúc (mặc định 0):

📅 Ngày đang xét: 2024-09-23
📅 Ngày giao dịch tiếp theo: 2024-09-24
📰 Các tin tức từ 2024-09-23 14:45:00 đến 2024-09-24 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-09-23:
 - Không có tin tức ảnh hưởng.
📊 Các khía cạnh cảm xúc (mặc định 0):

📅 Ngày đang xét: 2024-09-24
📅 Ngày 

DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.
DataFrame.applymap has been deprecated. Use DataFrame.map instead.



📅 Ngày đang xét: 2024-12-25
📅 Ngày giao dịch tiếp theo: 2024-12-26
📰 Các tin tức từ 2024-12-25 14:45:00 đến 2024-12-26 14:45:00 sẽ ảnh hưởng đến nhãn tại ngày 2024-12-25:
 - 2024-12-25 16:23:00: Dòng tiền bất ngờ đổ vào nhóm cổ phiếu đại gia Việt, VN-Index bứt phá cuối năm
   - Reputation: 0.0
   - Company Communication: 0.0
   - Appointment: 0.0
   - Financial: 0.5
   - Regulatory: 0.0
   - Sales: 0.0
   - M&A: 0.0
   - Legal: 0.0
   - Dividend Policy: 0.0
   - Risks: 0.0
   - Rumors: 0.0
   - Strategy: 0.3
   - Options: 0
   - IPO: 0.0
   - Signal: 0.4
   - Coverage: 0.0
   - Fundamentals: 0.3
   - Insider Activity: 0.0
   - Price Action: 0.6
   - Buyside: 0.0
   - Technical Analysis: 0.0
   - Trade: 0.0
   - Central Banks: 0.2
   - Currency: 0.1
   - Conditions: 0.0
   - Market: 0.5
   - Volatility: 0.3
   - Investor Sentiment: 0.4
   - Retail Investor Behavior: 0.3
   - Speculation: 0.2
   - Domestic Institutional Behavior: 0.0
   - Foreign Institutional Behavior: -0.1
   - Black 